In [1]:
%%bash
which python

/home/domenico/anaconda2/bin/python


In [2]:
from bs4 import BeautifulSoup
import pandas as pd
#import urllib2
import csv
import sys, os
import consts

Functions taken from `xml2tree.py` script

In [3]:
def parse_ins(x):
    n_ins = 0
    d = x
    pos, ins = d.split('.')
    # problem about 'XC' to be solved, so far
    # those events are not considered
    try:
        n_ins = int(ins[0])
        nat_ins = ins[1:]
        return '.'.join([pos, nat_ins*n_ins])
    except ValueError:
        pass

def retro_handle(i):
    # this function should be called before checking if the mutation is either a transition or a transversion.
    u = mut_handle(i.replace('!', ''))
    # an even number of "!" means that the change is actually occurring
    if i.count('!')%2 == 0:
        n = u
    # an odd number of "!" means that there is actually a retromutation
    else:
        n = u+'!'
    # check if the mutation is a transition or a transversion
    return n
 
def mut_handle(i):
    #print i
    # preliminar check of deletion
    if "." in i:
        n = parse_ins(i)
        if n is None:
            pass
    elif "d" in i:
        # in new phylotree versions deletions of single nts
        # are preceded by nt but have to be removed
        if i[0].isdigit() == False:
            n = i[1:]
        else:
            n = i
    else:
        x, y = [i[0].upper(), i[-1].upper()]
        if (x in consts.PUR and y in consts.PUR) or (x in consts.PYR and y in consts.PYR):
            # transition, from "G100A" get "100"
            n = i[1:-1]
        elif (x in consts.PUR and y in consts.PYR) or (x in consts.PYR and y in consts.PUR):
            # transversion, from "C100A" get "100A"
            n = i[1:].upper()
    return n
 

def events_parsing_string(string):
    # cfr events_parsing
    n_events = []
    events = string.split(',')
    # events between brackets are discarded
    events = [i for i in events if i[0] != '(']
    for e in events:
        # note: the function "retro_handle" handles all mutation types
        if "X" in e:
            print "%s, mutation ignored." % e
            continue
        e = retro_handle(e)
        if e is None:
            continue
        n_events.append(e)
    return n_events

def event_parsing(event):
    e = event
    # cfr events_parsing
    #n_events = []
    #events = string.split(',')
    # events between brackets are discarded
    #events = [i for i in events if i[0] != '(']
    #for e in events:
    # note: the function "retro_handle" handles all mutation types
    if "X" in e or "(" in e:
        print "%s, mutation ignored." % e
        E = ''
    else:
        E = retro_handle(e)
    if E is None:
        E = ''
    #    n_events.append(e)
    return E

In [4]:
def assignNoLabelStatus(s):
    status = "Label"
    s = s.strip(',').split(',')
    t = s[0]
    if len(t) > 1:
        # case to discard, eg C123G
        if t[0] in list('ACGT') and t[-1] in list('ACGT'):
            status = "NoLabel"
        # case to discard, eg C123G!
        elif t[0] in list('ACGT') and t[-1] == "!":
            status = "NoLabel"
        elif t[0].isalpha() == False:
            status = "NoLabel"
        # This last case replaces the next ones
        # case to discard, eg deletion 8123-8234d
        #elif t[0].isdigit() and t[-1] == "d":
        #    status = "NoLabel"
        # eg (C64T)
        #elif t[0] == "(":
        #    status = "NoLabel"
    return status

def checkIfAC(s):
    if len(s) > 0:
        if s[0].isalpha() and s[-1].isdigit(): # field is an AC
            return True
        elif s == "reserved":
            return True
        else:
            return False
    else:
        return False

In [5]:
#url = 'http://www.data.jma.go.jp/obd/stats/etrn/view/monthly_s3_en.php?block_no=47401&view=1'
#html = urllib2.urlopen(url).read()
html = open('mtDNA_tree_Build_17.onlytable.htm', 'r').read()
#print(repr(html))

In [6]:
soup = BeautifulSoup(html, 'lxml')

In [7]:
table = soup.find_all("table")[0]

In [8]:
rows = table.find_all("tr")

In [9]:
# col_normal = rows[6]

In [10]:
csv_list = []
o = open('phylotree_17_190121.csv', 'w')
for row in rows:
    try:
        #print "A row starts here"
        s = ""
        columns = row.find_all('td')
        #print columns
        #for column in columns:
        for x, column in enumerate(columns):
            #column_text = [event_parsing(f.replace("\A0", "")) for f in column.get_text().split()]
            column_text = [f.replace("\A0", "") for f in column.get_text().split()]
            column_text = [f for f in column_text if f != ""]
            #print column_text
            #if len(column_text) != 0:
            #    filled_field = True
            #print "{} field: {}, status: {}".format(x, column_text, filled_field)
            column_text = ','.join(column_text)
            #print column.get_text().split()
            #column_text = ','.join(column.get_text().split())
            s += "{},".format(column_text)
            #s = s.replace("\A0", "")
            #print s
        filled_field = False
        if s.strip(',') != "":
            #print(s)
            #print(s.rstrip(','))
            s_list = s.rstrip(',').split(',')#[:-1]
            # but first:
            # Delete ACs at the end
            while checkIfAC(s_list[-1]) == True:
                #print("Gonna reduce this: {}".format(s_list))
                s_list = s_list[:-1]
            #print(s_list)
            # Check if it's a NoLabel
            filled_field_occurrences = 0
            new_s_list = []
            print "OLD S: {}".format(','.join(s_list))
            for x,i in enumerate(s_list):
                if i != "": # leading fields
                    #print "Non empty field: {}".format(i)
                    # recognize haplogroup
                    filled_field_occurrences += 1
                    if filled_field_occurrences == 1:
                        if i == 'L0a1a' or i == "L0":
                            pass
                            #print s
                        status = assignNoLabelStatus(s)
                        if status == "NoLabel":
                            #print("Found NoLabel at {}".format(','.join(s_list)))
                            #s_list[x-1] = status
                            new_s_list = new_s_list[:-1]
                            new_s_list.append(status)
                            i = event_parsing(i)
                            if i != "":
                                new_s_list.append(i)
                            #break
                        else:
                            new_s_list.append(i)
                    else:
                        i = event_parsing(i)
                        if i == "C5899.d!":
                            print i
                            i = "5899.Cd!"
                        if i != "":
                            new_s_list.append(i)
                        #s_list[x] = i
                        #print s_list
                        # This are haplogroups, so check event.
                        #print(s_list)
                        #try:
                else:
                    #print "Empty field"
                    new_s_list.append(i)
            #while s_list[-1] == "":
            #    s_list = s_list[:-1]
            while new_s_list[-1] == "":
                new_s_list = new_s_list[:-1]
            #except:
    #            print("Error for:\n{}".format(s_list))
                #print(s_list)
            new_s = ','.join(new_s_list)
            print "NEW S: {}\n".format(new_s)
            if status == "NoLabel":
                pass
                #print new_s
            csv_list.append(new_s)
            o.write(new_s+"\n")
    except Exception, e:
        print e
        print "{}".format(columns)

o.close()

OLD S: L0,G263A,C1048T,C3516a,T5442C,T6185C,C9042T,A9347G,G10589A,G12007A,A12720G
NEW S: L0,263,1048,3516A,5442,6185,9042,9347,10589,12007,12720

OLD S: ,L0a'b'f'g'k,A189G,T4586C,C9818T,T16172C
NEW S: ,L0a'b'f'g'k,189,4586,9818,16172

OLD S: ,,L0a'b'f'g,G73A,G185A,C195T,A263G!,A2245G,C5603T,A11641G,C15136T,G15431A
NEW S: ,,L0a'b'f'g,73,185,195,263!,2245,5603,11641,15136,15431

OLD S: ,,,L0a'b'g,A93G,(A95c),T236C,C8428T,A8566G,G9755A,C16148T
(A95c), mutation ignored.
NEW S: ,,,L0a'b'g,93,236,8428,8566,9755,16148

OLD S: ,,,,L0a'g,G11176A,C16188g
NEW S: ,,,,L0a'g,11176,16188G

OLD S: ,,,,,L0a,C146T,G5231A,G5460A,T14308C,T16278C,C16320T
NEW S: ,,,,,L0a,146,5231,5460,14308,16278,16320

OLD S: ,,,,,,L0a1'4,C16168T
NEW S: ,,,,,,L0a1'4,16168

OLD S: ,,,,,,,L0a1,T5096C
NEW S: ,,,,,,,L0a1,5096

OLD S: ,,,,,,,,L0a1a,(C64T),T3866C,,,,,,,,,,,,,,
(C64T), mutation ignored.
NEW S: ,,,,,,,,L0a1a,3866

OLD S: ,,,,,,,,,,A200G,,,,,,,,,,,,,,
NEW S: ,,,,,,,,,NoLabel,200

OLD S: ,,,,,,,,,,L0a1a1,T2759C,,,,,

OLD S: ,,,,,,,,,,,L1c2b1b1,C264T,C3275g,C6173T,,,,,,,,,,,
NEW S: ,,,,,,,,,,,L1c2b1b1,264,3275G,6173

OLD S: ,,,,,,,,,L1c2b1c,A633G,A723G,G3421A,T3777C,T5580C,A5894d,T10071C,T15672C,C16292T,,,,,,,,,
NEW S: ,,,,,,,,,L1c2b1c,633,723,3421,3777,5580,5894d,10071,15672,16292

OLD S: ,,,,,,,,L1c2b2,T8567C,A13269G,C16320T,,,,,,,,,,,,,
NEW S: ,,,,,,,,L1c2b2,8567,13269,16320

OLD S: ,,,,,,L1c4,T151C!,T198C!,T5196C,A6629G,A7673G,A7960G,G9266A,A9545G,A13741G,T13879C,C16184T,C16301T
NEW S: ,,,,,,L1c4,151!,198!,5196,6629,7673,7960,9266,9545,13741,13879,16184,16301

OLD S: ,,,,,,,L1c4a,C280T,G1503A,G4596A,T4937C,G4959A,G5054A,A11337G,T11854C,G12940A,T14182C,T15191C,A16037G,T16093C,T16140C,,,,,,,
NEW S: ,,,,,,,L1c4a,280,1503,4596,4937,4959,5054,11337,11854,12940,14182,15191,16037,16093,16140

OLD S: ,,,,,,,L1c4b,A4706G,A11002G,,,,,,,,,,,,,,,
NEW S: ,,,,,,,L1c4b,4706,11002

OLD S: ,,,,,L1c6,G930A,A2251G,G5231A,T14470C,,,,,,,,,,,,,,,,
NEW S: ,,,,,L1c6,930,2251,5231,14470

OLD S: ,,,,L1c5,A291t,G709A,A539


OLD S: ,,,,,,,,,L3b2a,T5250C,T16189C!,,,,,,,,,,,,,
NEW S: ,,,,,,,,,L3b2a,5250,16189!

OLD S: ,,,,,,,,,L3b2b,G9053A,A9067G,C15550T,,,,,,,,,,,,
NEW S: ,,,,,,,,,L3b2b,9053,9067,15550

OLD S: ,,,,,,,,L3b3,G185A,A189G,A6527G,A9007G,C13934T,T14182C,G16048A,,,,,,,,,,,
NEW S: ,,,,,,,,L3b3,185,189,6527,9007,13934,14182,16048

OLD S: ,,,,,,,L3f,T3396C,T4218C,T15514C,T16209C
NEW S: ,,,,,,,L3f,3396,4218,15514,16209

OLD S: ,,,,,,,,L3f1,C5601T,T9950C
NEW S: ,,,,,,,,L3f1,5601,9950

OLD S: ,,,,,,,,,L3f1a,G3693A,C4350T,C5194T,A14148G,G15106A,,,,,,,,,,,
NEW S: ,,,,,,,,,L3f1a,3693,4350,5194,14148,15106

OLD S: ,,,,,,,,,,L3f1a1,T3197C,A12507G,,,,,,,,,,,,
NEW S: ,,,,,,,,,,L3f1a1,3197,12507

OLD S: ,,,,,,,,,L3f1b,A189G,(A200G),T1822C,C7819a,A8527G,C8932T,G11440A,A14769G,T16311C!
(A200G), mutation ignored.
NEW S: ,,,,,,,,,L3f1b,189,1822,7819A,8527,8932,11440,14769,16311!

OLD S: ,,,,,,,,,,,C16292T,,,,,,,,,,,,,
NEW S: ,,,,,,,,,,NoLabel,16292

OLD S: ,,,,,,,,,,,L3f1b1,C16295T,,,,,,,,,,,,
NEW S: ,,,,,,,,,,,L3

OLD S: ,,,,,,,,,,,,,M3c1b1a,G8856A,G16319A,,,,,,,,,
NEW S: ,,,,,,,,,,,,,M3c1b1a,8856,16319

OLD S: ,,,,,,,,,,,,,M3c1b1b,G15323A,,,,,,,,,,
NEW S: ,,,,,,,,,,,,,M3c1b1b,15323

OLD S: ,,,,,,,,,M3c2,T16154C,,,,,,,,,,,,,,
NEW S: ,,,,,,,,,M3c2,16154

OLD S: ,,,,,,,,M3d,T11827C,C16344T,,,,,,,,,,,,,,
NEW S: ,,,,,,,,M3d,11827,16344

OLD S: ,,,,,,,,,M3d1,T10238C,T13820C,,,,,,,,,,,,,
NEW S: ,,,,,,,,,M3d1,10238,13820

OLD S: ,,,,,,,,,,M3d1a,C12813T,,,,,,,,,,,,,
NEW S: ,,,,,,,,,,M3d1a,12813

OLD S: ,,,,,,,,,,,M3d1a1,A13836G,,,,,,,,,,,,
NEW S: ,,,,,,,,,,,M3d1a1,13836

OLD S: ,,,,,,,M4"67,G12007A
NEW S: ,,,,,,,M4"67,12007

OLD S: ,,,,,,,,,T16311C!
NEW S: ,,,,,,,,NoLabel,16311!

OLD S: ,,,,,,,,,M4,T6620C,G7859A,G16145A,C16261T
NEW S: ,,,,,,,,,M4,6620,7859,16145,16261

OLD S: ,,,,,,,,,,M4a,C16176T,,,,,,,,,,,,,
NEW S: ,,,,,,,,,,M4a,16176

OLD S: ,,,,,,,,,,M4b,T152C!,G15466A,T16086C,,,,,,,,,,,,
NEW S: ,,,,,,,,,,M4b,152!,15466,16086

OLD S: ,,,,,,,,,M65,C511T
NEW S: ,,,,,,,,,M65,511

OLD S: ,,,,,,,,,,M65a,

NEW S: ,,,,,,,,,M8a1,8453,15047,15148,15355,15697

OLD S: ,,,,,,,,,,M8a1a,T6719C,T16311C!,,,,,,,,,,,,
NEW S: ,,,,,,,,,,M8a1a,6719,16311!

OLD S: ,,,,,,,,,M8a2'3,C16184T
NEW S: ,,,,,,,,,M8a2'3,16184

OLD S: ,,,,,,,,,,M8a2,C2835T,,,,,,,,,,,,,
NEW S: ,,,,,,,,,,M8a2,2835

OLD S: ,,,,,,,,,,,,T152C!,,,,,,,,,,,,
NEW S: ,,,,,,,,,,,NoLabel,152!

OLD S: ,,,,,,,,,,,,M8a2a,G11176A,T16189C!,,,,,,,,,,
NEW S: ,,,,,,,,,,,,M8a2a,11176,16189!

OLD S: ,,,,,,,,,,,,,M8a2a1,G16470A,G16471A,,,,,,,,,
NEW S: ,,,,,,,,,,,,,M8a2a1,16470,16471

OLD S: ,,,,,,,,,,,,M8a2b,C4670T,T6671C,A13050G,,,,,,,,,
NEW S: ,,,,,,,,,,,,M8a2b,4670,6671,13050

OLD S: ,,,,,,,,,,,M8a2c,A15244G,,,,,,,,,,,,
NEW S: ,,,,,,,,,,,M8a2c,15244

OLD S: ,,,,,,,,,,,M8a2d,A234G,T9861C,G10646A,T12375C,C13993T,,,,,,,,,
NEW S: ,,,,,,,,,,,M8a2d,234,9861,10646,12375,13993

OLD S: ,,,,,,,,,,,M8a2e,G15217A,,,,,,,,,,,,
NEW S: ,,,,,,,,,,,M8a2e,15217

OLD S: ,,,,,,,,,,M8a3,C5100T,,,,,,,,,,,,,
NEW S: ,,,,,,,,,,M8a3,5100

OLD S: ,,,,,,,,,,,M8a3a,C16134T,,,,,,,

...

OLD S: ,,,,,,,,,,,,,,,F1a4b,T466C,G8251A,,,,,,,
NEW S: ,,,,,,,,,,,,,,,F1a4b,466,8251

OLD S: ,,,,,,,,,,,,,F1a2,T10034C,A16129G!!,,,,,,,,,
NEW S: ,,,,,,,,,,,,,F1a2,10034,16129

OLD S: ,,,,,,,,,,,,,,F1a2a,C16465T,,,,,,,,,
NEW S: ,,,,,,,,,,,,,,F1a2a,16465

OLD S: ,,,,,,,,,,,,,F1a3,T15565C
NEW S: ,,,,,,,,,,,,,F1a3,15565

OLD S: ,,,,,,,,,,,,,,,T16311C!,,,,,,,,,
NEW S: ,,,,,,,,,,,,,,NoLabel,16311!

OLD S: ,,,,,,,,,,,,,,,F1a3a,G9554A,T9944C,A13748G,,,,,,,
NEW S: ,,,,,,,,,,,,,,,F1a3a,9554,9944,13748

OLD S: ,,,,,,,,,,,,,,,,F1a3a1,A16129G!!,G16390A,,,,,,
NEW S: ,,,,,,,,,,,,,,,,F1a3a1,16129,16390

OLD S: ,,,,,,,,,,,,,,,,,F1a3a1a,T8705C,A16284G,,,,,
NEW S: ,,,,,,,,,,,,,,,,,F1a3a1a,8705,16284

OLD S: ,,,,,,,,,,,,,,,,F1a3a2,C150T,C4011T,T16189C!,,,,,,
NEW S: ,,,,,,,,,,,,,,,,F1a3a2,150,4011,16189!

OLD S: ,,,,,,,,,,,,,,,,F1a3a3,C15452T,,,,,,,
NEW S: ,,,,,,,,,,,,,,,,F1a3a3,15452

OLD S: ,,,,,,,,,,,,,,,,,F1a3a3a,G14323A,,,,,,
NEW S: ,,,,,,,,,,,,,,,,,F1a3a3a,14323

OLD S: ,,,,,,,,,,,,,,F1a3b,G53A,G54c,


OLD S: ,,,,,,,,,,,,,,,,,,B2i2a1b,A3843G,,,,,
NEW S: ,,,,,,,,,,,,,,,,,,B2i2a1b,3843

OLD S: ,,,,,,,,,,,,,,,,B2i2b,G207A,,,,,,,
NEW S: ,,,,,,,,,,,,,,,,B2i2b,207

OLD S: ,,,,,,,,,,,,,,,,,B2i2b1,A153G,T16249C,,,,,
NEW S: ,,,,,,,,,,,,,,,,,B2i2b1,153,16249

OLD S: ,,,,,,,,,,,,,,B2j,T131C,A183G,C5270T,A15924G,A16166G,G16361A,,,,,,
NEW S: ,,,,,,,,,,,,,,B2j,131,183,5270,15924,16166,16361

OLD S: ,,,,,,,,,,,,,,B2k,T146C!,T4371C,,,,,,,,
NEW S: ,,,,,,,,,,,,,,B2k,146!,4371

OLD S: ,,,,,,,,,,,,,,B2l,T16422C,,,,,,,,,
NEW S: ,,,,,,,,,,,,,,B2l,16422

OLD S: ,,,,,,,,,,,,,,B2m,A15766G,A16164G,C16519a,,,,,,,
NEW S: ,,,,,,,,,,,,,,B2m,15766,16164,16519A

OLD S: ,,,,,,,,,,,,,,B2n,A4191G,G6383A,,,,,,,,
NEW S: ,,,,,,,,,,,,,,B2n,4191,6383

OLD S: ,,,,,,,,,,,,,,B2o,T16092C,,,,,,,,,
NEW S: ,,,,,,,,,,,,,,B2o,16092

OLD S: ,,,,,,,,,,,,,,,B2o1,T7270C,G16145A,,,,,,,
NEW S: ,,,,,,,,,,,,,,,B2o1,7270,16145

OLD S: ,,,,,,,,,,,,,,,,B2o1a,T152C!,A14500G,,,,,,
NEW S: ,,,,,,,,,,,,,,,,B2o1a,152!,14500

OLD S: ,,,,,,,,,,,,,,B


OLD S: ,,,,,,,,,,,,,,,,,T16093C,,,,,,,
NEW S: ,,,,,,,,,,,,,,,,NoLabel,16093

OLD S: ,,,,,,,,,,,,,,,,,U5a1b1d1,C198T,,,,,,
NEW S: ,,,,,,,,,,,,,,,,,U5a1b1d1,198

OLD S: ,,,,,,,,,,,,,,,U5a1b1e,A12582G,,,,,,,,
NEW S: ,,,,,,,,,,,,,,,U5a1b1e,12582

OLD S: ,,,,,,,,,,,,,,,U5a1b1f,G15596A,G16129A!,,,,,,,
NEW S: ,,,,,,,,,,,,,,,U5a1b1f,15596,16129!

OLD S: ,,,,,,,,,,,,,,,U5a1b1g,T11353C,,,,,,,,
NEW S: ,,,,,,,,,,,,,,,U5a1b1g,11353

OLD S: ,,,,,,,,,,,,,,,U5a1b1h,A10754G,,,,,,,,
NEW S: ,,,,,,,,,,,,,,,U5a1b1h,10754

OLD S: ,,,,,,,,,,,,,,U5a1b2,A9632G,,,,,,,,,
NEW S: ,,,,,,,,,,,,,,U5a1b2,9632

OLD S: ,,,,,,,,,,,,,,,T16362C,,,,,,,,,
NEW S: ,,,,,,,,,,,,,,NoLabel,16362

OLD S: ,,,,,,,,,,,,,,,U5a1b3,G16428A,,,,,,,,
NEW S: ,,,,,,,,,,,,,,,U5a1b3,16428

OLD S: ,,,,,,,,,,,,,,,,U5a1b3a,A5153G,,,,,,,
NEW S: ,,,,,,,,,,,,,,,,U5a1b3a,5153

OLD S: ,,,,,,,,,,,,,,,,,U5a1b3a1,A249G,,,,,,
NEW S: ,,,,,,,,,,,,,,,,,U5a1b3a1,249

OLD S: ,,,,,,,,,,,,,,,U5a1b4,A12331G,,,,,,,,
NEW S: ,,,,,,,,,,,,,,,U5a1b4,12331

OLD S: ,,,,,

OLD S: ,,,,,,,,,,,,U2a2,C194T,G3316A,A4970G,T5201C,G7382A,G7853A,G7859A,C11151T,T11299C,T12477C,G12561A,C14883T,G15734A,T16271C,,
NEW S: ,,,,,,,,,,,,U2a2,194,3316,4970,5201,7382,7853,7859,11151,11299,12477,12561,14883,15734,16271

OLD S: ,,,,,,,,,,,U2b,T146C!,G2706A,A5186t,C12106T,G13194A,C15049T
NEW S: ,,,,,,,,,,,U2b,146!,2706,5186T,12106,13194,15049

OLD S: ,,,,,,,,,,,,U2b1,G3915A,A4093G,(C16168T),,,,,,,,,
(C16168T), mutation ignored.
NEW S: ,,,,,,,,,,,,U2b1,3915,4093

OLD S: ,,,,,,,,,,,,,U2b1a,G13708A,,,,,,,,,,
NEW S: ,,,,,,,,,,,,,U2b1a,13708

OLD S: ,,,,,,,,,,,,U2b2,T152C!,A234G,G1888A,C9094T,A9614G,T12793C,T13656C,G15930A,T16209C,C16239T,T16352C,C16353T,,,
NEW S: ,,,,,,,,,,,,U2b2,152!,234,1888,9094,9614,12793,13656,15930,16209,16239,16352,16353

OLD S: ,,,,,,,,,,,,T152C!
NEW S: ,,,,,,,,,,,NoLabel,152!

OLD S: ,,,,,,,,,,,,U2c'd,C16234T
NEW S: ,,,,,,,,,,,,U2c'd,16234

OLD S: ,,,,,,,,,,,,,U2c,C5790a,T14935C,A15061G,,,,,,,,
NEW S: ,,,,,,,,,,,,,U2c,5790A,14935,15061

OLD S: ,,,,,,,,,,,


OLD S: ,,,,,,,,,,,,,,,,,,,K1a4a1f,T152C!,C325T,A10029G,,
NEW S: ,,,,,,,,,,,,,,,,,,,K1a4a1f,152!,325,10029

OLD S: ,,,,,,,,,,,,,,,,,,,,K1a4a1f1,T217C,T5774C,,
NEW S: ,,,,,,,,,,,,,,,,,,,,K1a4a1f1,217,5774

OLD S: ,,,,,,,,,,,,,,,,,,,K1a4a1g,A8149G,C16287T,,,
NEW S: ,,,,,,,,,,,,,,,,,,,K1a4a1g,8149,16287

OLD S: ,,,,,,,,,,,,,,,,,,,K1a4a1h,T13404C,,,,
NEW S: ,,,,,,,,,,,,,,,,,,,K1a4a1h,13404

OLD S: ,,,,,,,,,,,,,,,,,,,K1a4a1i,A6260G!,A15880G,,,
NEW S: ,,,,,,,,,,,,,,,,,,,K1a4a1i,6260!,15880

OLD S: ,,,,,,,,,,,,,,,,,K1a4b,C280g,A9448G,,,,,
NEW S: ,,,,,,,,,,,,,,,,,K1a4b,280G,9448

OLD S: ,,,,,,,,,,,,,,,,,,K1a4b1,T6975C,A7388G,C8410T,A13105G!,,,
NEW S: ,,,,,,,,,,,,,,,,,,K1a4b1,6975,7388,8410,13105!

OLD S: ,,,,,,,,,,,,,,,,,K1a4c,T152C!,A12612G,A13827G,,,,,
NEW S: ,,,,,,,,,,,,,,,,,K1a4c,152!,12612,13827

OLD S: ,,,,,,,,,,,,,,,,,,K1a4c1,C5264T,A13710G,A16246t,,,
NEW S: ,,,,,,,,,,,,,,,,,,K1a4c1,5264,13710,16246T

OLD S: ,,,,,,,,,,,,,,,,,K1a4d,A723c,C11071T,G15355A,,,,,
NEW S: ,,,,,,,,,,,,,,,,,K1a4d

In [11]:
it = 'phylotree_17_190121.csv'

In [12]:
ot = 'phylotree_17_190127.csv'

In [13]:
f = open(it,'r')
f = f.readlines()
o = open(ot,'w')

In [14]:
dic_h = {}
c = 0
for branch in f:
	branch = branch.split(',')
	dic_h[c]=''
	new_line = ""
	for x in xrange(len(branch)):
		if branch[x] == '':
			pass
		else:
			if branch[x] != "NoLabel" and branch[x][0].isupper():
				dic_h[c] = (x,branch[x])
				#print dic_h[c],c,branch
				new_line = map(lambda x:str(x),branch)
				new_line = ','.join(new_line).strip()
				#o.write(new_line+'\n')
				break
			elif branch[x] == "NoLabel":
				print ','.join(branch).strip()
				#print 'Here is the problem',c,x
				z = c-1
				while z > 0:
					#print dic_h[z],z,branch[x],x
					if dic_h[z][0] < x:
						distance = str(c-z)
						#print "distance",distance
						new_label = dic_h[z][1]+"_"+str(branch[x+1]).strip()
						dic_h[c] = (x,new_label)
						branch[x] = new_label
						new_line = map(lambda x:str(x),branch)
						new_line = ','.join(new_line).strip()
						break
						#o.write(new_line+'\n')
					else:
						z = z-1
			else:
				pass
	if new_line == "":
		sys.exit("{} yielded an empty new line.".format(branch))
	else:
		if "_" in new_line: print new_line + '\n'
		o.write(new_line+'\n')
	c += 1

,,,,,,,,,NoLabel,200
,,,,,,,,,L0a1a_200,200

,,,,,,,,NoLabel,16293
,,,,,,,,L0a1_16293,16293

,,,,,,NoLabel,152
,,,,,,L0d1b1_152,152

,,,,,NoLabel,189
,,,,,L1b1a_189,189

,,,,,,,,NoLabel,198!
,,,,,,,,L1c1a_198!,198!

,,,,,,,,NoLabel,16189!
,,,,,,,,L2a1_16189!,16189!

,,,,,,,,,,NoLabel,143
,,,,,,,,,,L2a1b_143,143

,,,,,,,,NoLabel,143
,,,,,,,,L2a1_143,143

,,,,,,,,,,NoLabel,16086
,,,,,,,,,,L2a1c_16086,16086

,,,,,,,,,,NoLabel,16129!
,,,,,,,,,,L2a1c_16129!,16129!

,,,,,,,,,NoLabel,16309!
,,,,,,,,,L2a1_143_16309!,16309!

,,,,,,,,,NoLabel,16189!
,,,,,,,,,L2a1_143_16189!,16189!

,,,,,,,,,,NoLabel,16309!
,,,,,,,,,,L2a1_143_16189!_16309!,16309!

,,,,,,,NoLabel,16129!
,,,,,,,L2d_16129!,16129!

,,,,,,,NoLabel,709
,,,,,,,L3a_709,709

,,,,,,,,,,NoLabel,152!
,,,,,,,,,,L3b1a_152!,152!

,,,,,,,,,,NoLabel,16124!
,,,,,,,,,,L3b1a_16124!,16124!

,,,,,,,,,,NoLabel,16292
,,,,,,,,,,L3f1b_16292,16292

,,,,,,,,,,,NoLabel,150
,,,,,,,,,,,L3f1b_16292_150,150

,,,,,,,,,,NoLabel,152!
,,,,,,,,,,L3e2b_152!,152!

,,,,


,,,,,,,,,,,,,,NoLabel,146!
,,,,,,,,,,,,,,T2b6_146!,146!

,,,,,,,,,,,,,NoLabel,150
,,,,,,,,,,,,,T2b_150,150

,,,,,,,,,,,,,NoLabel,16362
,,,,,,,,,,,,,T2b_16362,16362

,,,,,,,,,,,,,NoLabel,152!
,,,,,,,,,,,,,T2b_152!,152!

,,,,,,,,,,,,,,NoLabel,146!
,,,,,,,,,,,,,,T2c1_146!,146!

,,,,,,,,,,,,,,,,NoLabel,152!
,,,,,,,,,,,,,,,,T2c1d_152!,152!

,,,,,,,,,,,,NoLabel,150
,,,,,,,,,,,,T2_150,150

,,,,,,,,,,,,,,NoLabel,152!
,,,,,,,,,,,,,,T2e_152!,152!

,,,,,,,,,,,,NoLabel,16189!
,,,,,,,,,,,,T2_16189!,16189!

,,,,,,,,,NoLabel,16129!
,,,,,,,,,R6_16129!,16129!

,,,,,,,,,,,NoLabel,16093
,,,,,,,,,,,R8a1_16093,16093

,,,,,,,,,,,,,,NoLabel,16311!
,,,,,,,,,,,,,,F1a3_16311!,16311!

,,,,,,,,,,,NoLabel,16189!
,,,,,,,,,,,F1_16189!,16189!

,,,,,,,,,,,,,,NoLabel,152
,,,,,,,,,,,,,,F1b1_152,152

,,,,,,,,,,,NoLabel,16291
,,,,,,,,,,,F2_16291,16291

,,,,,,,,,,,,,NoLabel,16291!
,,,,,,,,,,,,,F2a_16291!,16291!

,,,,,,,,,,,NoLabel,195!
,,,,,,,,,,,F2_195!,195!

,,,,,,,,,,,,NoLabel,207
,,,,,,,,,,,,F3a_207,207

,,,,,,,,,,,,N

In [15]:
o.close()

In [16]:
import getopt, sys, re, os, glob, csv
from classifier import tree, NGclassify, consts, datatypes, parse_mhcs
from bioinf.seqs import SeqList
import io_modules.csv
import io_modules.old_table
import io_modules.serialize
import pandas as pd
import os.path
sys.setrecursionlimit(100000)

In [17]:
csvfile = 'phylotree_17_190127.csv'
out_fname = 'haplogroups'

In [18]:
#write pickle file for MToolBox
tree_file = csv.reader(open(csvfile, 'rb'))

pickle_fname = csvfile + '.pickle'
aplo_list = io_modules.csv.parse_csv(tree_file)
htree = tree.HaplogroupTree(aplo_list=aplo_list)
pickle_file = open(pickle_fname, 'wb')
pickle_file.write(htree.serialize())
pickle_file.close()
#write out alleles and haplogroups defined for HmtDB in csv file
pickle_file = pickle_fname
out_file = out_fname + '.csv'
htree = tree.HaplogroupTree(pickle_data=open(pickle_file, 'rb').read())
fh = csv.writer(open(out_file, 'wb'))
for haplo_name in htree:
	io_modules.old_table.write_haplogroup(fh, '', htree[haplo_name])

#write haplogrups.txt tab delimited file for MToolBox
out_file2 = out_fname + '.txt'
hap_file = pd.read_csv(out_file,sep=',',header=None)
subset = hap_file[[0,1,3]]
subset.dropna(inplace=True)
alleles = subset[1].astype(str).str.cat(subset[3])
subset.insert(1,'Allele',alleles)
subset = subset[[0,'Allele']]
subset.columns=['haplogroup_code','POSITIONnucleotidic_change']
subset.to_csv(out_file2,sep='\t',header=True,index=None)


CIAO
M7c1c3(1)
[Transition(769), Transition(15236), Transition(3606), Transition(16129), Transition(4104), Transition(3594), Transition(5442), Transition(11665), Transition(15043), Transition(8468), Transition(16278), Transition(152), Transition(15301), Transition(10400), Transition(10915), Transition(10664), Transition(13105), Transition(16311), Transition(7256), Transversion(825), Transition(10810), Transition(12091), Transition(11914), Transition(14783), Transition(10688), Transition(13506), Transition(195), Transition(2885), Transition(2758), Transition(199), Transition(6455), Transition(8655), Transition(13650), Transition(4312), Transition(13276), Transition(9824), Transition(7521), Transition(16187), Transition(16230), Transition(4071), Transition(489), Transition(16362), Transition(16189), Transition(4850), Transition(247), Transition(1018), Transition(7146)]
CIAO
M7c1c2(2)
[Transition(769), Transition(15236), Transition(3606), Transition(16129), Transition(4104), Transition(35

B4a2b1a(2)
[Transition(8448), Transition(16261), Transition(15247), Transition(10771), Transition(16217), Transition(16153), Transition(9114), Transition(5465), Transition(9123), Transition(13759), Transversion(72), Transition(210), Transition(9812), Deletion(8281), Transition(5082), Transition(13711), Transition(6620), Transition(13413), Transition(16360), Transition(9069), Transition(14071), Transversion(7930), Transition(10876)]
CIAO
Y2a1(1)
[Transition(12161), Transition(769), Transition(4104), Transition(11914), Transition(15244), Transition(14914), Transition(7256), Transition(146), Transition(8468), Transition(16278), Transition(152), Transition(5147), Transition(16129), Transition(6941), Transition(11299), Transition(10664), Transition(5417), Transition(13105), Transition(7859), Transversion(825), Transition(10810), Transition(16187), Transition(3594), Transition(10688), Transition(13506), Transition(195), Transition(9540), Transition(2885), Transition(2758), Transition(8392), 

[Transition(16278), Transition(16391), Transition(4104), Transition(1836), Transition(3594), Transition(7256), Transition(146), Transition(15043), Transition(8468), Transition(3990), Transition(152), Transversion(4529), Transversion(8616), Insertion(455), Transition(16172), Transition(13488), Transition(13105), Transition(10034), Transition(15924), Transition(1719), Transversion(825), Transition(10810), Transition(8251), Transition(769), Transition(11914), Transition(10688), Transition(13506), Transition(195), Transition(9540), Transition(2885), Transition(2758), Transition(199), Transition(204), Transition(6734), Transition(8655), Transition(13650), Transition(13780), Transition(12501), Transition(203), Transition(4312), Transition(9947), Transition(13276), Transition(250), Transition(7521), Transition(16187), Transition(16230), Transition(7146), Transition(10664), Transition(4023), Transition(3447), Transition(10873), Transition(1018), Transition(8701), Transition(10238), Transition(

CIAO
W3a1a2(2)
[Transition(769), Transition(16129), Transition(4104), Transition(11914), Transition(13263), Transversion(15884), Transition(194), Transition(7256), Transition(146), Transition(8468), Transition(16278), Transition(152), Transition(11674), Transition(7151), Transition(10398), Transition(709), Transition(8994), Transition(10915), Transition(16292), Transition(9127), Transition(15784), Transition(11947), Transition(2885), Transition(3505), Transition(5046), Transition(16311), Transversion(825), Transition(10810), Transition(8251), Transition(3594), Transition(10688), Transition(13506), Transition(9540), Transition(2758), Transition(204), Transition(207), Transition(5585), Transition(13650), Transition(5460), Transition(1243), Transition(4312), Transition(8655), Transition(13276), Transition(13105), Transition(7521), Transition(16187), Transition(16230), Transition(7146), Transition(16189), Transition(10664), Transition(12414), Transition(189), Transition(247), Transition(10

CIAO
D4b1a1(7)
[Transition(769), Transition(8450), Transition(13827), Transition(16129), Transition(4104), Transition(3594), Transition(14091), Transition(3010), Transition(7256), Transition(146), Transition(4883), Transition(8468), Transition(16278), Transition(10181), Transition(10400), Transition(10915), Transition(2246), Transition(10664), Transition(13105), Transition(15951), Transition(16311), Transversion(825), Transversion(5178), Transition(16187), Transition(11914), Transition(14783), Transition(10688), Transition(13506), Transition(15043), Transition(15301), Transition(2758), Transition(16189), Transition(14668), Transition(14927), Transition(15440), Transition(13650), Transition(8020), Transition(4312), Transition(8655), Transition(13276), Transition(10810), Transition(8414), Transition(7521), Transition(16230), Transition(489), Transition(16362), Transition(15805), Transition(15217), Transition(2885), Transition(247), Transition(1018), Transition(16319), Transition(7146), T

...

CIAO
L1c1'2'4'5'6(1)
[Transition(12810), Transition(7055), Transition(146), Transition(151), Transition(10915), Transition(16294), Transition(10664), Transition(297), Transition(13485), Transition(13789), Transversion(14000), Transition(182), Transition(6071), Transversion(186), Transition(316), Transversion(189), Transition(5951), Transition(11914), Transition(3666), Transition(4312), Transition(10586), Transition(8027), Transition(13276), Transition(7389), Transition(14560), Transition(14178), Transition(16230), Transition(16360), Transition(9072), Deletion(2395), Transition(14911)]
CIAO
L5b(4)
[Transition(11914), Transition(12432), Transition(146), Transition(16148), Transition(12950), Transition(152), Transition(10915), Transition(7972), Transition(16166), Transition(10664), Transition(13105), Transition(16311), Transition(2885), Transition(2758), Insertion(459), Transition(4312), Transition(13276), Transition(3423), Transition(16230), Transition(7146), Transition(8468), Transition

CIAO
M21b_210(1)
[Transition(769), Transition(16129), Transition(4104), Transition(3594), Transition(7256), Transition(146), Transition(15043), Transition(8468), Transition(16278), Transition(152), Transition(15301), Transition(10400), Transition(10915), Transition(10664), Transition(13105), Transition(7861), Transition(16311), Transversion(825), Transition(10810), Transition(16187), Transition(11914), Transition(14783), Transition(10688), Transition(13506), Transition(195), Transition(2885), Transition(2758), Transition(3915), Transition(8655), Transition(13650), Transition(4312), Transition(11482), Transition(13276), Transition(7521), Transition(16230), Transition(489), Transition(7146), Transition(210), Transition(16189), Transition(5108), Transition(247), Transition(1018)]
CIAO
D4l2a(1)
[Transition(769), Transition(16129), Transition(4104), Transition(3594), Transition(3010), Transition(7256), Transition(146), Transition(4883), Transition(8468), Transition(16278), Transition(152), 

[Transition(8448), Transition(4742), Transition(16140), Transition(15247), Transition(16274), Transition(10771), Transition(3221), Transition(150), Deletion(8281), Transition(16153), Transition(16154), Transition(9114), Transition(3497), Transition(13759), Transition(5826), Transition(709), Insertion(455), Transversion(72), Transition(13879), Transition(14162), Transition(211), Transition(16217), Transition(5082), Transition(13711), Transition(1119), Transition(7909), Transition(210), Transition(16111), Transition(16497), Transition(15346), Transition(14071), Transversion(7930)]
CIAO
M7c(4)
[Transition(769), Transition(16129), Transition(4104), Transition(3594), Transition(11665), Transition(15043), Transition(8468), Transition(16278), Transition(152), Transition(15301), Transition(10400), Transition(10915), Transition(11914), Transition(10664), Transition(13105), Transition(16311), Transition(7256), Transversion(825), Transition(10810), Transition(12091), Transition(16189), Transition

CIAO
Z4a1a(1)
[Transition(769), Transition(9090), Transition(16260), Transition(5894), Transition(16129), Transition(8584), Transition(3594), Transition(7256), Transition(146), Transition(15043), Transition(8468), Transition(16278), Transversion(7196), Transition(15301), Transition(10400), Transition(10915), Transition(15784), Transition(16298), Transition(16302), Transition(13105), Transition(16311), Transition(16185), Transition(10810), Transition(16187), Transition(11914), Transition(14783), Transition(10688), Transition(13506), Transition(195), Transition(2885), Transition(2758), Deletion(15944), Transition(8655), Transition(13650), Transversion(825), Transition(4312), Transition(13276), Transition(6752), Transition(7521), Transition(16230), Transition(489), Transition(7146), Transition(4715), Transition(10664), Transition(15475), Transition(5492), Transition(4104), Transition(247), Deletion(249), Transition(1018), Transversion(15487)]
CIAO
F1b(7)
[Transition(8448), Transition(3970

/home/domenico/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


### Display parent nodes of a given haplogroup

In [19]:
htree.get_haplogroup_branch('X2b4a')

[X2b4a(1),
 X2b4(1),
 X2b_226(1),
 X2b(2),
 X2b'd(1),
 X2_225(1),
 X2(2),
 X1'2'3(1),
 X(6),
 A2z(7),
 A2s(10),
 A2r1(2),
 A2r(1),
 A2aq(6),
 A2ap(1),
 _16189!(1)]

Number in brackets is the number of mutations added by that haplogroup to the parent nodes leading to it, _eg_ X2b4a adds one mutation to the parent nodes bringing to him. The problem is that **\_16189!**. For some reason there is a bunch of NoLabel that are being converted in a bad way, eg:

**phyotree csv with "NoLabel"**

In [21]:
%%bash
grep -A 4 A2an phylotree_17_190121.csv

,,,,,,,,,,,,A2an,8772
,,,,,,,,,,,,NoLabel,16189!
,,,,,,,,,,,,,A2ap,9809
,,,,,,,,,,,,A2aq,143,808,3421,6267,6374,16355
,,,,,,,,,,,A2r,6935


**phyotree csv with names assigned to "NoLabel"**

In [22]:
%%bash
grep -A 4 A2an phylotree_17_190127.csv

,,,,,,,,,,,,A2an,8772
,,,,,,,,,,,,NoLabel
_16189!,16189!
,,,,,,,,,,,,,A2ap,9809
,,,,,,,,,,,,A2aq,143,808,3421,6267,6374,16355
